# Quadrotor2D Lidar System - Complete Framework Demonstration

This script demonstrates ALL framework capabilities using the Quadrotor2D with LIDAR observations:
- Symbolic system definition with complex observation function
- Output feedback control design (LQG)
- Extended Kalman Filter for nonlinear state estimation
- Neural Lyapunov function training
- Comprehensive ROA analysis (Monte Carlo, Sobol QMC, Halton QMC)
- 2D and 3D Lyapunov visualizations
- Output feedback error sensitivity analysis
- Trajectory simulation and visualization
- Phase portraits (2D and 3D)
- Performance metrics and verification

The Quadrotor2DLidar system:
- State: [y, θ, ẏ, θ̇] (vertical position, pitch, velocities)
- Control: [u1, u2] (thrust from each rotor)
- Output: [lidar_0, lidar_1, lidar_2, lidar_3] (4 distance measurements)
- Partial observability requires state estimation

In [1]:
# imports 
import sys

# Add repository root to Python path
sys.path.append("../")

import torch
import torch.nn as nn
import numpy as np
from neural_lyapunov_training.symbolic_systems import SymbolicQuadrotor2DLidar
from neural_lyapunov_training.symbolic_dynamics import (
    GenericDiscreteTimeSystem,
    IntegrationMethod,
    LinearController,
    LinearObserver,
    ExtendedKalmanFilter,
)
from neural_lyapunov_training.lyapunov_roa_visualization import (
    plot_lyapunov_2d,
    plot_lyapunov_3d_surface,
    plot_lyapunov_2d_error_slices,
)
from neural_lyapunov_training.roa_metrics import (
    compute_lyapunov_difference_metrics_qmc_sobol,
    compute_lyapunov_difference_metrics_qmc_halton,
    compute_lyapunov_difference_metrics_monte_carlo,
    compare_lyapunov_difference_methods,
    print_lyapunov_difference_metrics,
)

In [2]:
# necessary class and function definitions
class AugmentedLyapunovNetwork(nn.Module):
    """
    Lyapunov function for output feedback: V([x, e])

    For observer-based control, the Lyapunov function operates on
    augmented state [x, e] where:
    - x: physical state (4D)
    - e: estimation error (4D)
    Total input: 8D
    """

    def __init__(self, state_dim, hidden_dim=64):
        super().__init__()
        # Input is augmented state [x, e]
        input_dim = 2 * state_dim
        self.input_dim = input_dim
        
        self.net = nn.Sequential(
            nn.Linear(input_dim, hidden_dim),
            nn.Tanh(),
            nn.Linear(hidden_dim, hidden_dim),
            nn.Tanh(),
            nn.Linear(hidden_dim, hidden_dim),
            nn.Tanh(),
            nn.Linear(hidden_dim, 1),
        )

        with torch.no_grad():
            for layer in self.net:
                if isinstance(layer, nn.Linear):
                    nn.init.xavier_normal_(layer.weight, gain=0.1)
                    nn.init.zeros_(layer.bias)

    def forward(self, z):
        """
        Evaluate V([x, e])

        Args:
            z: Augmented state (batch, 2*nx) = [x, e]
        """
        V_raw = self.net(z)
        # Ensure positive and zero at origin
        z_norm_sq = (z**2).sum(dim=-1, keepdim=True)
        V = z_norm_sq + 0.1 * torch.relu(V_raw)
        return V


class AugmentedControllerNetwork(nn.Module):
    """
    Controller for output feedback: u = π([x_hat, y])

    Takes observer estimate and current measurement as input.
    """

    def __init__(self, state_dim, output_dim, control_dim, hidden_dim=32):
        super().__init__()
        # Input is [x_hat, y]
        input_dim = state_dim + output_dim
        self.input_dim = input_dim
        self.control_dim = control_dim

        self.net = nn.Sequential(
            nn.Linear(input_dim, hidden_dim),
            nn.Tanh(),
            nn.Linear(hidden_dim, hidden_dim),
            nn.Tanh(),
            nn.Linear(hidden_dim, control_dim),
        )

        with torch.no_grad():
            for layer in self.net:
                if isinstance(layer, nn.Linear):
                    nn.init.xavier_normal_(layer.weight, gain=0.5)
                    nn.init.zeros_(layer.bias)

    def forward(self, x_hat_y):
        """Controller expects [x_hat, y] concatenated"""
        return self.net(x_hat_y)


class LuenbergerObserver(nn.Module):
    """
    Luenberger observer: x_hat[k+1] = f(x_hat[k], u[k]) + L(y[k+1] - h(x_hat[k+1]))

    Uses linear gain L but nonlinear dynamics f and observation h.
    """

    def __init__(self, dynamics_system, L):
        super().__init__()
        self.dynamics = dynamics_system
        self.L = torch.tensor(L, dtype=torch.float32)
        self.nx = dynamics_system.nx
        self.x_hat = dynamics_system.x_equilibrium.clone()

    def forward(self, x_hat, u, y_next):
        """
        Observer update

        Args:
            x_hat: Current estimate (batch, nx)
            u: Control (batch, nu)
            y_next: Next measurement (batch, ny)

        Returns:
            x_hat_next: Updated estimate (batch, nx)
        """
        # Predict
        x_hat_pred = self.dynamics(x_hat, u)

        # Predicted measurement
        y_pred = self.dynamics.h(x_hat_pred)

        # Innovation
        innovation = y_next - y_pred

        # Correction
        correction = (self.L @ innovation.unsqueeze(-1)).squeeze(-1)
        x_hat_next = x_hat_pred + correction

        return x_hat_next
    
    def reset(self, x0: torch.Tensor | None = None):
        """
        Reset observer to initial state estimate.

        Args:
            x0: Initial state estimate (nx,). Uses equilibrium if None.
        """
        if x0 is not None:
            self.x_hat = x0.clone()
        else:
            self.x_hat = self.dynamics.x_equilibrium.clone()
    
    def to(self, device):
        """
        Move observer to specified device (CPU/GPU).

        Args:
            device: torch.device or string ('cpu', 'cuda')

        Returns:
            Self for chaining
        """
        self.L = self.L.to(device)
        self.x_hat = self.x_hat.to(device)
        return self


def train_output_feedback_lyapunov(
    system, controller_nn, observer_nn, num_samples=5000, num_epochs=300
):
    """
    Train Lyapunov function for output feedback system

    Trains V([x, e]) where e is estimation error
    """
    print("\nTraining output feedback Lyapunov function...")

    lyapunov_nn = AugmentedLyapunovNetwork(system.nx, hidden_dim=64)
    optimizer = torch.optim.Adam(lyapunov_nn.parameters(), lr=1e-3)

    for epoch in range(num_epochs):
        # Sample physical states
        x_samples = torch.randn(num_samples, system.nx) * 0.3

        # Sample estimation errors (typically smaller than states)
        e_samples = torch.randn(num_samples, system.nx) * 0.1

        # Augmented state [x, e]
        z_samples = torch.cat([x_samples, e_samples], dim=1)

        # Current V([x, e])
        V_current = lyapunov_nn(z_samples)

        # Evolve closed-loop system
        x_true = x_samples
        x_hat = x_true - e_samples

        # Get measurement
        y = system.h(x_true)

        # Augment for controller
        x_hat_y = torch.cat([x_hat, y], dim=1)
        u = controller_nn(x_hat_y)

        # Evolve physical state
        x_next = system(x_true, u)

        # Next measurement
        y_next = system.h(x_next)

        # Evolve observer
        x_hat_next = observer_nn(x_hat, u, y_next)

        # Next estimation error
        e_next = x_next - x_hat_next

        # Next augmented state
        z_next = torch.cat([x_next, e_next], dim=1)
        V_next = lyapunov_nn(z_next)

        # Losses
        V_origin = lyapunov_nn(torch.zeros(1, 2 * system.nx))
        loss_origin = V_origin**2

        delta_V = V_next - V_current
        loss_decrease = torch.relu(delta_V + 0.01).mean()
        loss_magnitude = V_current.mean() * 0.01

        loss = loss_origin + loss_decrease + loss_magnitude

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        if (epoch + 1) % 50 == 0 or epoch == 0:
            with torch.no_grad():
                violations = (delta_V > 0).sum().item()
                print(
                    f"  Epoch {epoch+1:3d}: Loss={loss.item():.4f}, "
                    f"V(0)={V_origin.item():.6f}, "
                    f"Violations={violations}/{num_samples} ({100*violations/num_samples:.1f}%)"
                )

    print("  ✓ Training complete")
    return lyapunov_nn

In [3]:
# System parameters
quad = SymbolicQuadrotor2DLidar(
    length=0.25,  # Rotor arm length
    mass=0.486,  # Mass (kg)
    inertia=0.00383,  # Moment of inertia
    gravity=9.81,  # Gravity
    b=0.1,  # Damping
    H=5.0,  # Max lidar range
    angle_max=0.149 * np.pi,  # Lidar FOV
    origin_height=1.0,  # Height offset
)

quad.print_equations(simplify=False)

SymbolicQuadrotor2DLidar
State Variables: [y, theta, y_dot, theta_dot]
Control Variables: [u1, u2]
System Order: 2
Dimensions: nx=4, nu=2, ny=4

Dynamics: dx/dt = f(x, u)
  dy/dt = -0.1*y_dot + 2.05761316872428*(u1 + u2)*cos(theta) - 9.81
  dtheta/dt = -0.1*theta_dot + 65.2741514360313*u1 - 65.2741514360313*u2

Output: y = h(x)
  y[0] = (y + 1.0)/(4*cos(theta + 0.468097305384879)) + sqrt((y + 1.0)**2/cos(theta + 0.468097305384879)**2 + 1.0e-6)/4 - sqrt((-(y + 1.0)/(2*cos(theta + 0.468097305384879)) - sqrt((y + 1.0)**2/cos(theta + 0.468097305384879)**2 + 1.0e-6)/2 + 5.0)**2 + 1.0e-6)/2 + 2.5
  y[1] = (y + 1.0)/(4*cos(theta + 0.156032435128293)) + sqrt((y + 1.0)**2/cos(theta + 0.156032435128293)**2 + 1.0e-6)/4 - sqrt((-(y + 1.0)/(2*cos(theta + 0.156032435128293)) - sqrt((y + 1.0)**2/cos(theta + 0.156032435128293)**2 + 1.0e-6)/2 + 5.0)**2 + 1.0e-6)/2 + 2.5
  y[2] = (y + 1.0)/(4*cos(theta - 0.156032435128293)) + sqrt((y + 1.0)**2/cos(theta - 0.156032435128293)**2 + 1.0e-6)/4 - sqrt((-(y + 

In [4]:
# Create discrete system
dt = 0.01  # 100 Hz
discrete_system = GenericDiscreteTimeSystem(
    quad, dt, integration_method=IntegrationMethod.RK4
)
print(f"\nEquilibrium (hover):")
print(f"  State: {quad.x_equilibrium}")
print(f"  Control: {quad.u_equilibrium} (equal thrust)")


Equilibrium (hover):
  State: tensor([0., 0., 0., 0.])
  Control: tensor([2.3838, 2.3838]) (equal thrust)


In [5]:
# LQR costs
Q_lqr = np.diag([100.0, 50.0, 10.0, 5.0])  # Penalize position and angle
R_lqr = np.eye(2) * 0.1

# Kalman filter noise covariances
Q_process = np.diag([0.01, 0.01, 0.1, 0.1])  # Process noise
R_measurement = np.eye(4) * 0.5  # Lidar measurement noise

K, L = discrete_system.dlqg_control(Q_lqr, R_lqr, Q_process, R_measurement)

print(f"LQR gain K shape: {K.shape}")
print(f"Kalman gain L shape: {L.shape}")

LQR gain K shape: (2, 4)
Kalman gain L shape: (4, 4)


In [6]:
# Verify closed-loop stability
A_cl = discrete_system.dlqg_closed_loop_matrix(K, L)
eigs_cl = np.linalg.eigvals(A_cl)
is_stable = np.all(np.abs(eigs_cl) < 1)
print(f"Closed-loop stable: {is_stable}")
print(f"Max |λ|: {np.max(np.abs(eigs_cl)):.4f}")

Closed-loop stable: True
Max |λ|: 0.9678


In [7]:
# Create linear controller and observer
linear_controller = LinearController(K, quad.x_equilibrium, quad.u_equilibrium)
linear_controller.K = linear_controller.K.float()
linear_controller.x_eq = linear_controller.x_eq.float()
linear_controller.u_eq = linear_controller.u_eq.float()

linear_observer = LinearObserver(discrete_system, L)

In [8]:
# Neural controller (takes [x_hat, y])
nn_controller = AugmentedControllerNetwork(
    state_dim=quad.nx, output_dim=quad.ny, control_dim=quad.nu, hidden_dim=32
)

# Neural observer (Luenberger with constant gain)
nn_observer = LuenbergerObserver(discrete_system, L)

print(
    f"  Controller input: {quad.nx} (state) + {quad.ny} (measurement) = {quad.nx + quad.ny}"
)
print(f"  Controller output: {quad.nu} (control)")
print(f"  Observer: Luenberger with Kalman gain L")

  Controller input: 4 (state) + 4 (measurement) = 8
  Controller output: 2 (control)
  Observer: Luenberger with Kalman gain L


In [9]:
lyapunov_nn = train_output_feedback_lyapunov(
    discrete_system, nn_controller, nn_observer, num_samples=8000, num_epochs=1000
)

# Verify V(0, 0) = 0
V_eq = lyapunov_nn(torch.zeros(1, 2 * discrete_system.nx))
print(f"\nV([0, 0]) = {V_eq.item():.6f} (should be ≈ 0)")


Training output feedback Lyapunov function...
  Epoch   1: Loss=0.0504, V(0)=0.000000, Violations=4637/8000 (58.0%)
  Epoch  50: Loss=0.0498, V(0)=0.000000, Violations=4584/8000 (57.3%)
  Epoch 100: Loss=0.0490, V(0)=0.000000, Violations=4539/8000 (56.7%)
  Epoch 150: Loss=0.0498, V(0)=0.000000, Violations=4545/8000 (56.8%)
  Epoch 200: Loss=0.0485, V(0)=0.000000, Violations=4581/8000 (57.3%)
  Epoch 250: Loss=0.0489, V(0)=0.000000, Violations=4607/8000 (57.6%)
  Epoch 300: Loss=0.0498, V(0)=0.000000, Violations=4610/8000 (57.6%)
  Epoch 350: Loss=0.0502, V(0)=0.000000, Violations=4702/8000 (58.8%)
  Epoch 400: Loss=0.0487, V(0)=0.000000, Violations=4577/8000 (57.2%)
  Epoch 450: Loss=0.0498, V(0)=0.000000, Violations=4683/8000 (58.5%)
  Epoch 500: Loss=0.0477, V(0)=0.000000, Violations=4514/8000 (56.4%)
  Epoch 550: Loss=0.0486, V(0)=0.000000, Violations=4536/8000 (56.7%)
  Epoch 600: Loss=0.0493, V(0)=0.000000, Violations=4627/8000 (57.8%)
  Epoch 650: Loss=0.0491, V(0)=0.000000, Vi

In [10]:
# Analyze in (y, θ) subspace (position and angle)
state_indices_analysis = (0, 1)  # y and θ
state_limits_analysis = (
    (-2.0, 2.0),  # y: ±2m vertical position
    (-np.pi / 4, np.pi / 4),  # θ: ±45° pitch angle
)

# Estimate ρ from boundary with multiplier = 0.85
boundary_samples = []
for y_val in [state_limits_analysis[0][0], state_limits_analysis[0][1]]:
    for theta_val in np.linspace(
        state_limits_analysis[1][0], state_limits_analysis[1][1], 20
    ):
        x = torch.zeros(4, dtype=torch.float32)
        x[0] = y_val
        x[1] = theta_val
        e = torch.zeros(4, dtype=torch.float32)
        z = torch.cat([x, e])
        boundary_samples.append(z)

with torch.no_grad():
    V_boundary = lyapunov_nn(torch.stack(boundary_samples))
    rho = V_boundary.min().item() * 0.85

print(f"Estimated ρ = {rho:.4f}")

Estimated ρ = 3.4015


In [11]:
# Compare all sampling methods
print("\nComparing all ROA estimation methods...")
all_methods = compare_lyapunov_difference_methods(
    lyapunov_nn,
    nn_controller,
    discrete_system,
    state_limits_analysis,
    rho,
    num_samples=30000,
    observer_nn=nn_observer,
    state_indices=state_indices_analysis,
    compute_discrepancy=True,
)

# Use Sobol results for detailed analysis
sobol_metrics = all_methods["qmc_sobol"]
print_lyapunov_difference_metrics(
    sobol_metrics, title="Quadrotor2D Lidar ROA Analysis"
)


Comparing all ROA estimation methods...
Computing Lyapunov difference via Monte Carlo (random)...


Computing Lyapunov difference via Quasi-Monte Carlo (Sobol)...


/home/benezer.gi/ondemand/dev/CS-7268-Verifiable-Machine-Learning/Lyapunov_Stable_NN_Controllers_Custom_Dynamics/framework_demo_notebooks/../neural_lyapunov_training/roa_metrics.py:142: UserWarning: Rounded n_samples from 30000 to 32768 (power of 2) for optimal Sobol sequence properties.
  warnings.warn(


Computing Lyapunov difference via Quasi-Monte Carlo (Halton)...

                                    Method Comparison                                     
Method               ROA Vol      Verified Vol % Verified   Mean ΔV     
------------------------------------------------------------------------------------------
monte_carlo          5.624289     0.000000     0.00       % 0.013325    
qmc_sobol            5.614178     0.000000     0.00       % 0.013347    
qmc_halton           5.613188     0.000000     0.00       % 0.013347    

                            Discrepancy (lower = more uniform)                            
------------------------------------------------------------------------------------------
  qmc_sobol           : 9.906431e-10
  qmc_halton          : 2.054682e-09


                         Quadrotor2D Lidar ROA Analysis                         

                                 Configuration                                  
---------------------------------------

In [42]:
print("Simulating with linear observer (LQG)...")

# Initial conditions with estimation error
x0_true = torch.tensor([1.0, np.deg2rad(20), 0.0, 0.0], dtype=torch.float32)
x0_estimate = torch.tensor([0.5, np.deg2rad(10), 0.0, 0.0], dtype=torch.float32)

linear_observer.reset(x0=x0_estimate)

horizon = 1000  # 10 seconds
trajectory_true = [x0_true]
trajectory_estimate = [x0_estimate]
controls = []

x_true = x0_true
for t in range(horizon):
    # Measurement with noise
    y_measured = discrete_system.h(x_true) + torch.randn(quad.ny) * 0.05

    # Control based on estimate
    u = linear_controller(linear_observer.x_hat)

    # Update observer
    linear_observer.update(u, y_measured, dt=discrete_system.dt)

    # Update true system
    x_true = discrete_system(x_true, u)

    trajectory_true.append(x_true)
    trajectory_estimate.append(linear_observer.x_hat)
    controls.append(u)

traj_true_linear = torch.stack(trajectory_true)
traj_est_linear = torch.stack(trajectory_estimate)

print(f"  Simulation complete: {horizon} steps")
print(
    f"  Final estimation error: {torch.norm(traj_true_linear[-1] - traj_est_linear[-1]).item():.4f}"
)

Simulating with linear observer (LQG)...
  Simulation complete: 1000 steps
  Final estimation error: 0.0636


In [43]:
print("Simulating with Extended Kalman Filter...")

ekf = ExtendedKalmanFilter(discrete_system, Q_process, R_measurement)
ekf.reset(x0=x0_estimate)

trajectory_ekf = [x0_estimate]
covariance_trace = [torch.trace(ekf.P).item()]

x_true = x0_true
for t in range(horizon):
    y_measured = discrete_system.h(x_true) + torch.randn(quad.ny) * 0.05
    u = linear_controller(ekf.x_hat)

    ekf.predict(u, dt=discrete_system.dt)
    ekf.update(y_measured)

    x_true = discrete_system(x_true, u)
    trajectory_ekf.append(ekf.x_hat)
    covariance_trace.append(torch.trace(ekf.P).item())

traj_ekf = torch.stack(trajectory_ekf)

print(f"  EKF simulation complete")
print(
    f"  Final estimation error: {torch.norm(traj_true_linear[-1] - traj_ekf[-1]).item():.4f}"
)
print(f"  Final covariance trace: {covariance_trace[-1]:.4f}")

Simulating with Extended Kalman Filter...
  EKF simulation complete
  Final estimation error: 0.1641
  Final covariance trace: 7.2840


In [44]:
print("Comparing observer performance...")

error_linear = traj_true_linear - traj_est_linear
error_ekf = traj_true_linear[:-1] - traj_ekf[:-1]  # EKF has one less point

rmse_linear = error_linear.pow(2).mean(dim=0).sqrt()
rmse_ekf = error_ekf.pow(2).mean(dim=0).sqrt()

print(f"\n  Linear Observer RMSE:")
print(f"    y: {rmse_linear[0]:.4f}, θ: {rmse_linear[1]:.4f}")
print(f"    ẏ: {rmse_linear[2]:.4f}, θ̇: {rmse_linear[3]:.4f}")

print(f"\n  Extended Kalman Filter RMSE:")
print(f"    y: {rmse_ekf[0]:.4f}, θ: {rmse_ekf[1]:.4f}")
print(f"    ẏ: {rmse_ekf[2]:.4f}, θ̇: {rmse_ekf[3]:.4f}")

Comparing observer performance...

  Linear Observer RMSE:
    y: 0.0243, θ: 0.0186
    ẏ: 0.1874, θ̇: 0.0754

  Extended Kalman Filter RMSE:
    y: 0.0551, θ: 0.0288
    ẏ: 0.1592, θ̇: 0.1077


In [15]:
print("Simulating multiple initial conditions...")

ics_physical = [
    torch.tensor([1.5, np.deg2rad(30), 0.0, 0.0], dtype=torch.float32),
    torch.tensor([-1.5, np.deg2rad(-30), 0.0, 0.0], dtype=torch.float32),
    torch.tensor([1.0, np.deg2rad(20), 0.5, 0.5], dtype=torch.float32),
    torch.tensor([-1.0, np.deg2rad(-20), -0.5, -0.5], dtype=torch.float32),
]

ic_names = [
    "High right (+1.5m, +30°)",
    "Low left (-1.5m, -30°)",
    "Moving up-right",
    "Moving down-left",
]

# Simulate with linear observer
trajectories_multi = []
for ic in ics_physical:
    nn_observer.reset(x0=quad.x_equilibrium)
    traj_true = [ic]
    x = ic

    for t in range(horizon):
        y = discrete_system.h(x) + torch.randn(quad.ny) * 0.05
        controller_input = torch.cat([nn_observer.x_hat, y])
        u = nn_controller(controller_input)
        nn_observer.forward(nn_observer.x_hat, u, y)
        x = discrete_system(x, u)
        traj_true.append(x)

    trajectories_multi.append(torch.stack(traj_true))

print(f"  Simulated {len(trajectories_multi)} trajectories")

Simulating multiple initial conditions...


  Simulated 4 trajectories


In [16]:
# plotting 2D Lyapunov function, position and angle
plot_lyapunov_2d(
        lyapunov_nn,
        nn_controller,
        discrete_system,
        state_limits_analysis,
        state_indices=state_indices_analysis,
        state_names=("Vertical Position y [m]", "Pitch Angle θ [rad]"),
        rho=rho,
        grid_resolution=100,
        observer_nn=nn_observer,
        trajectories=trajectories_multi,
        title="Quadrotor2D Lidar: Lyapunov Function (Output Feedback, Neural)",
        save_html="quadrotor_lidar_lyapunov_2d_neural.html",
        show=False,
        colorscale="Viridis",
        trajectory_colorscale="Vivid",
    )

z_estimate shape: torch.Size([10000, 4])
y shape: torch.Size([10000, 4])
Controller expects: 8
Lyapunov visualization saved to quadrotor_lidar_lyapunov_2d_neural.html


In [48]:
# simulating with linear controllers and observers
ics_physical = [
    torch.tensor([1.5, np.deg2rad(30), 0.0, 0.0], dtype=torch.float32),
    torch.tensor([-1.5, np.deg2rad(-30), 0.0, 0.0], dtype=torch.float32),
    torch.tensor([1.0, np.deg2rad(20), 0.5, 0.5], dtype=torch.float32),
    torch.tensor([-1.0, np.deg2rad(-20), -0.5, -0.5], dtype=torch.float32),
]

ic_names = [
    "High right (+1.5m, +30°)",
    "Low left (-1.5m, -30°)",
    "Moving up-right",
    "Moving down-left",
]

# Simulate with linear observer
trajectories_multi = []
for ic in ics_physical:
    linear_observer.reset(x0=quad.x_equilibrium)
    traj_true = [ic]
    x = ic

    for t in range(horizon):
        y = discrete_system.h(x) + torch.randn(quad.ny) * 0.05
        u = linear_controller(linear_observer.x_hat)
        linear_observer.update(u, y, dt=dt)
        x = discrete_system(x, u)
        traj_true.append(x)

    trajectories_multi.append(torch.stack(traj_true))

print(f"  Simulated {len(trajectories_multi)} trajectories")

  Simulated 4 trajectories


In [18]:
# plotting 2D Lyapunov function, position and angle
plot_lyapunov_2d(
        lyapunov_nn,
        nn_controller,
        discrete_system,
        state_limits_analysis,
        state_indices=state_indices_analysis,
        state_names=("Vertical Position y [m]", "Pitch Angle θ [rad]"),
        rho=rho,
        grid_resolution=100,
        observer_nn=nn_observer,
        title="Quadrotor2D Lidar: Lyapunov Function (Output Feedback, Neural)",
        show=False,
        colorscale="Viridis",
    )

z_estimate shape: torch.Size([10000, 4])
y shape: torch.Size([10000, 4])
Controller expects: 8


In [19]:
# plotting 2D Lyapunov function, velocities
state_limits_vel = ((-2, 2), (-1.0, 1.0))
state_indices_vel = (2, 3)

plot_lyapunov_2d(
    lyapunov_nn,
    nn_controller,
    discrete_system,
    state_limits_vel,
    state_indices=state_indices_vel,
    state_names=("Vertical Velocity ẏ [m/s]", "Angular Velocity θ̇ [rad/s]"),
    rho=rho,
    grid_resolution=100,
    observer_nn=nn_observer,
    title="Quadrotor2D Lidar: Lyapunov Function (Velocity Space, Output Feedback, Neural)",
    show=False,
    colorscale="Plasma",
)

z_estimate shape: torch.Size([10000, 4])
y shape: torch.Size([10000, 4])
Controller expects: 8


In [20]:
# 3D Lyapunov function, only function, position and angle
plot_lyapunov_3d_surface(
        lyapunov_nn,
        state_limits_analysis,
        controller_nn=nn_controller,
        dynamics_system=discrete_system,
        observer_nn=nn_observer,
        state_indices=state_indices_analysis,
        state_names=("Vertical Position y [m]", "Pitch Angle θ [rad]"),
        rho=rho,
        grid_resolution=60,
        title="Quadrotor2D Lidar: V(y, θ) - Output Feedback, Neural",
        show=False,
        colorscale="Viridis",
    )

In [21]:
# 3D Lyapunov function, function and derivative, position and angle
plot_lyapunov_3d_surface(
        lyapunov_nn,
        state_limits_analysis,
        controller_nn=nn_controller,
        dynamics_system=discrete_system,
        observer_nn=nn_observer,
        state_indices=state_indices_analysis,
        state_names=("Vertical Position y [m]", "Pitch Angle θ [rad]"),
        rho=rho,
        grid_resolution=60,
        title="Quadrotor2D Lidar: Lyapunov and Derivative (Output Feedback, Neural)",
        show=False,
        colorscale="Viridis",
        show_derivative=True,
    )

z_estimate shape: torch.Size([3600, 4])
y shape: torch.Size([3600, 4])
Controller expects: 8


In [22]:
# 3D Lyapunov function, function and derivative, velocities
plot_lyapunov_3d_surface(
        lyapunov_nn,
        state_limits_vel,
        controller_nn=nn_controller,
        dynamics_system=discrete_system,
        observer_nn=nn_observer,
        state_indices=state_indices_vel,
        state_names=("Vertical Velocity [m/s]", "Angular Velocity [rad/s]"),
        rho=rho,
        grid_resolution=60,
        title="Quadrotor2D Lidar: Lyapunov and Derivative (Output Feedback, Neural, Velocities)",
        show=False,
        colorscale="Viridis",
        show_derivative=True,
    )

z_estimate shape: torch.Size([3600, 4])
y shape: torch.Size([3600, 4])
Controller expects: 8


In [23]:
state_limits_pos = ((-2, 2), (-2, 2))
state_indices_pos = (0, 2)

# 3D Lyapunov function, function and derivative, position and derivative
plot_lyapunov_3d_surface(
        lyapunov_nn,
        state_limits_pos,
        controller_nn=nn_controller,
        dynamics_system=discrete_system,
        observer_nn=nn_observer,
        state_indices=state_indices_pos,
        state_names=("Vertical Position [m]", "Vertical Velocity [m/s]"),
        rho=rho,
        grid_resolution=60,
        title="Quadrotor2D Lidar: Lyapunov and Derivative (Output Feedback, Neural, Position and Derivative)",
        show=False,
        colorscale="Viridis",
        show_derivative=True,
    )

z_estimate shape: torch.Size([3600, 4])
y shape: torch.Size([3600, 4])
Controller expects: 8


In [24]:
state_limits_angle = ((-2, 2), (-2, 2))
state_indices_angle = (1, 3)

# 3D Lyapunov function, function and derivative, angle and derivative
plot_lyapunov_3d_surface(
        lyapunov_nn,
        state_limits_angle,
        controller_nn=nn_controller,
        dynamics_system=discrete_system,
        observer_nn=nn_observer,
        state_indices=state_indices_angle,
        state_names=("Angular Position [rad]", "Angular Velocity [rad/s]"),
        rho=rho,
        grid_resolution=60,
        title="Quadrotor2D Lidar: Lyapunov and Derivative (Output Feedback, Neural, Angle and Derivative)",
        show=False,
        colorscale="Viridis",
        show_derivative=True,
    )

z_estimate shape: torch.Size([3600, 4])
y shape: torch.Size([3600, 4])
Controller expects: 8


In [25]:
# error slice plot (def needs debugging w.r.t. color bar and legend positioning)
plot_lyapunov_2d_error_slices(
        lyapunov_nn,
        nn_controller,
        discrete_system,
        nn_observer,
        state_limits_analysis,
        error_values=[0.0, 0.1, 0.3, 0.5],
        error_dim=0,  # Error in y (vertical position)
        state_indices=state_indices_analysis,
        state_names=("Vertical Position y [m]", "Pitch Angle θ [rad]"),
        rho=rho,
        grid_resolution=80,
        title="Quadrotor2D: Impact of Position Estimation Error",
        show=False,
    )

In [49]:
# Compare true state vs estimate
comparison_trajs = torch.stack([traj_true_linear, traj_est_linear])

discrete_system.plot_trajectory(
    comparison_trajs,
    state_names=[
        "Vertical Position y [m]",
        "Pitch Angle θ [rad]",
        "Vertical Velocity ẏ [m/s]",
        "Angular Velocity θ̇ [rad/s]",
    ],
    trajectory_names=["True State", "Observer Estimate"],
    title="Quadrotor2D Lidar: True State vs Observer Estimate",
    colorway="Set1",
    show=False,
)

Plotting 2 trajectories...


In [50]:
# Plot estimation error
error_traj = (traj_true_linear - traj_est_linear).unsqueeze(0)

discrete_system.plot_trajectory(
    error_traj,
    state_names=[
        "Position Error Δy [m]",
        "Angle Error Δθ [rad]",
        "Velocity Error Δẏ [m/s]",
        "Angular Vel Error Δθ̇ [rad/s]",
    ],
    title="Quadrotor2D Lidar: Observer Estimation Error",
    colorway="Reds",
    show=False,
)

Plotting 1 trajectories...


In [51]:
# Multiple initial conditions
all_trajs_multi = torch.stack(trajectories_multi)

discrete_system.plot_trajectory(
    all_trajs_multi,
    state_names=[
        "Vertical Position y [m]",
        "Pitch Angle θ [rad]",
        "Vertical Velocity ẏ [m/s]",
        "Angular Velocity θ̇ [rad/s]",
    ],
    trajectory_names=ic_names,
    title="Quadrotor2D Lidar: Multiple Initial Conditions",
    colorway="Dark24",
    show=False,
)

Plotting 4 trajectories...
Interactive plot saved to quadrotor_lidar_trajectories_multi.html (size: 1050x700px)


In [52]:
# 2D phase portrait, position and angle
discrete_system.plot_phase_portrait_2d(
    all_trajs_multi,
    state_indices=(0, 1),
    state_names=("Vertical Position y [m]", "Pitch Angle θ [rad]"),
    trajectory_names=ic_names,
    title="Quadrotor2D Lidar: Phase Portrait (y-θ)",
    colorway="Dark24",
    show=False,
)


In [53]:
# 2D phase portrait, velocities
discrete_system.plot_phase_portrait_2d(
    all_trajs_multi,
    state_indices=(2, 3),
    state_names=("Vertical Velocity ẏ [m/s]", "Angular Velocity θ̇ [rad/s]"),
    trajectory_names=ic_names,
    title="Quadrotor2D Lidar: Phase Portrait (ẏ-θ̇)",
    colorway="Dark24",
    show=False,
)

In [54]:
# 3D phase portrait, position and angle and vertical velocity
discrete_system.plot_phase_portrait_3d(
    all_trajs_multi,
    state_indices=(0, 1, 2),
    state_names=(
        "Vertical Position y [m]",
        "Pitch Angle θ [rad]",
        "Vertical Velocity ẏ [m/s]",
    ),
    trajectory_names=ic_names,
    title="Quadrotor2D Lidar: 3D Phase Portrait (y-θ-ẏ)",
    colorway="Dark24",
    show=False,
    show_time_markers=True,
    marker_interval=25,
)

In [55]:
# 3D phase portrait, angle and velocities
discrete_system.plot_phase_portrait_3d(
        all_trajs_multi,
        state_indices=(1, 2, 3),
        state_names=(
            "Pitch Angle θ [rad]",
            "Vertical Velocity ẏ [m/s]",
            "Angular Velocity θ̇ [rad/s]",
        ),
        trajectory_names=ic_names,
        title="Quadrotor2D Lidar: 3D Phase Portrait (θ-ẏ-θ̇)",
        colorway="Dark24",
        show=False,
        show_time_markers=True,
        marker_interval=25,
    )

In [56]:
for i, (traj, name) in enumerate(zip(trajectories_multi, ic_names)):
        with torch.no_grad():
            # Augment with zero error for ideal behavior analysis
            e_zero = torch.zeros_like(traj)
            z_traj = torch.cat([traj, e_zero], dim=1)
            V_traj = lyapunov_nn(z_traj).squeeze()

        delta_V_traj = V_traj[1:] - V_traj[:-1]

        print(f"\n  Trajectory {i+1}: {name}")
        print(f"    Initial V([x₀, 0])      = {V_traj[0].item():.4f}")
        print(f"    Final V([x_f, 0])       = {V_traj[-1].item():.4f}")
        print(f"    Total decrease          = {V_traj[0].item() - V_traj[-1].item():.4f}")
        print(f"    Min ΔV                  = {delta_V_traj.min().item():.6f}")
        print(f"    Max ΔV                  = {delta_V_traj.max().item():.6f}")
        print(f"    Mean ΔV                 = {delta_V_traj.mean().item():.6f}")
        print(f"    Stays in ROA (below ρ)  = {(V_traj <= rho).all()}")
        print(f"    End at equilibrium      = {torch.allclose(z_traj[-1], torch.cat([discrete_system.x_equilibrium, e_zero[-1].squeeze()]))}")


  Trajectory 1: High right (+1.5m, +30°)
    Initial V([x₀, 0])      = 2.5242
    Final V([x_f, 0])       = 0.0245
    Total decrease          = 2.4996
    Min ΔV                  = -2.966206
    Max ΔV                  = 7.948172
    Mean ΔV                 = -0.002500
    Stays in ROA (below ρ)  = False
    End at equilibrium      = False

  Trajectory 2: Low left (-1.5m, -30°)
    Initial V([x₀, 0])      = 2.5242
    Final V([x_f, 0])       = 0.0434
    Total decrease          = 2.4807
    Min ΔV                  = -1.180983
    Max ΔV                  = 2.147364
    Mean ΔV                 = -0.002481
    Stays in ROA (below ρ)  = False
    End at equilibrium      = False

  Trajectory 3: Moving up-right
    Initial V([x₀, 0])      = 1.6218
    Final V([x_f, 0])       = 0.0065
    Total decrease          = 1.6153
    Min ΔV                  = -1.148366
    Max ΔV                  = 3.368787
    Mean ΔV                 = -0.001615
    Stays in ROA (below ρ)  = False
    End at equi

In [57]:
discrete_system.print_info(include_equations=False, include_linearization=True)

Discrete-Time System: SymbolicQuadrotor2DLidar

Discretization:
  Time step (dt):        0.01
  Integration method:    RK4
  Position integration:  RK4

Dimensions:
  State dimension (nx):    4
  Control dimension (nu):  2
  Output dimension (ny):   4
  System order:            2
  Generalized coords (nq): 2

Equilibrium:
  x_eq = [0. 0. 0. 0.]
  u_eq = [2.38383 2.38383]

----------------------------------------------------------------------
Linearization at Equilibrium:
----------------------------------------------------------------------
Continuous-time (Ac, Bc):
  Ac =
[[ 0.   0.   1.   0. ]
 [ 0.   0.   0.   1. ]
 [ 0.   0.  -0.1  0. ]
 [ 0.   0.   0.  -0.1]]
  Bc =
[[  0.          0.       ]
 [  0.          0.       ]
 [  2.0576131   2.0576131]
 [ 65.274155  -65.274155 ]]

Discrete-time (Ad, Bd) with dt=0.01:
  Ad =
[[1.    0.    0.01  0.   ]
 [0.    1.    0.    0.01 ]
 [0.    0.    0.999 0.   ]
 [0.    0.    0.    0.999]]
  Bd =
[[ 0.          0.        ]
 [ 0.          0.      